# ASL- Fingerspelling 

## What is American Sign Language Fingerspelling Recognition ?

American Sign Language Fingerspelling Recognition is a technology that uses computer vision and machine learning algorithms to recognize and interpret the hand gestures used in American Sign Language (ASL) fingerspelling. It can be used to create tools and applications that help people with hearing impairments to communicate more effectively with others. The technology involves comparing the input image of the hand gesture to a pre-defined set of templates, extracting relevant features from the input image, or training a neural network on a large dataset of ASL fingerspelling images to learn the patterns and features that are most important for recognition. Despite some challenges, ASL Fingerspelling Recognition has the potential to greatly improve the lives of people with hearing impairments.

## Data Overview

### Files
#### [train/supplemental_metadata].csv


* path - The path to the landmark file.
* file_id - A unique identifier for the data file.
* participant_id - A unique identifier for the data contributor.
* sequence_id - A unique identifier for the landmark sequence. Each data file may contain many sequences.
* phrase - The labels for the landmark sequence. The train and test datasets contain randomly generated addresses, phone numbers, and urls derived from components of real addresses/phone numbers/urls. Any overlap with real addresses, phone numbers, or urls is purely accidental. The supplemental dataset consists of fingerspelled sentences. Note that some of the urls include adult content. The intent of this competition is to support the Deaf and Hard of Hearing community in engaging with technology on an equal footing with other adults.

### character_to_prediction_index.json

#### [train/supplemental]_landmarks/ 
The landmark data. The landmarks were extracted from raw videos with the MediaPipe holistic model. Not all of the frames necessarily had visible hands or hands that could be detected by the model.
The landmark files contain the same data as in the ASL Signs competition (minus the row ID column) but reshaped into a wide format. This allows you to take advantage of the Parquet format to entirely skip loading landmarks that you aren't using.

* sequence_id - A unique identifier for the landmark sequence. Most landmark files contain 1,000 sequences. The sequence ID is used as the dataframe index.
* frame - The frame number within a landmark sequence.
* [x/y/z]_[type]_[landmark_index] - There are now 1,629 spatial coordinate columns for the x, y and z coordinates for each of the 543 landmarks. The type of landmark is one of ['face', 'left_hand', 'pose', 'right_hand']. Details of the hand landmark locations can be found here. The spatial coordinates have already been normalized by MediaPipe. Note that the MediaPipe model is not fully trained to predict depth so you may wish to ignore the z values. The landmarks have been converted to float32.

In [36]:
### import libraries
import pandas as pd,numpy as np,os
import json
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.io as pio
from pathlib import Path
pio.templates.default = "simple_white"
print("importing..")

importing..


In [37]:
def map_new_to_old_style(sequence):
    types = []
    landmark_indexes = []
    for column in list(sequence.columns)[1:544]:
        parts = column.split("_")
        if len(parts) == 4:
            types.append(parts[1] + "_" + parts[2])
        else:
            types.append(parts[1])

        landmark_indexes.append(int(parts[-1]))

    data = {
        "frame": [],
        "type": [],
        "landmark_index": [],
        "x": [],
        "y": [],
        "z": []
    }

    for index, row in sequence.iterrows():
        data["frame"] += [int(row.frame)]*543
        data["type"] += types
        data["landmark_index"] += landmark_indexes

        for _type, landmark_index in zip(types, landmark_indexes):
            data["x"].append(row[f"x_{_type}_{landmark_index}"])
            data["y"].append(row[f"y_{_type}_{landmark_index}"])
            data["z"].append(row[f"z_{_type}_{landmark_index}"])

    return pd.DataFrame.from_dict(data)

# assign desired colors to landmarks
def assign_color(row):
    if row == 'face':
        return 'red'
    elif 'hand' in row:
        return 'dodgerblue'
    else:
        return 'green'

# specifies the plotting order
def assign_order(row):
    if row.type == 'face':
        return row.landmark_index + 101
    elif row.type == 'pose':
        return row.landmark_index + 30
    elif row.type == 'left_hand':
        return row.landmark_index + 80
    else:
        return row.landmark_index
    
def visualise2d_landmarks(parquet_df, title=""):
    connections = [  
        [0, 1, 2, 3, 4,],
        [0, 5, 6, 7, 8],
        [0, 9, 10, 11, 12],
        [0, 13, 14, 15, 16],
        [0, 17, 18, 19, 20],

        
        [38, 36, 35, 34, 30, 31, 32, 33, 37],
        [40, 39],
        [52, 46, 50, 48, 46, 44, 42, 41, 43, 45, 47, 49, 45, 51],
        [42, 54, 56, 58, 60, 62, 58],
        [41, 53, 55, 57, 59, 61, 57],
        [54, 53],

        
        [80, 81, 82, 83, 84, ],
        [80, 85, 86, 87, 88],
        [80, 89, 90, 91, 92],
        [80, 93, 94, 95, 96],
        [80, 97, 98, 99, 100], ]

    parquet_df = map_new_to_old_style(parquet_df)
    frames = sorted(set(parquet_df.frame))
    first_frame = min(frames)
    parquet_df['color'] = parquet_df.type.apply(lambda row: assign_color(row))
    parquet_df['plot_order'] = parquet_df.apply(lambda row: assign_order(row), axis=1)
    first_frame_df = parquet_df[parquet_df.frame == first_frame].copy()
    first_frame_df = first_frame_df.sort_values(["plot_order"]).set_index('plot_order')


    frames_l = []
    for frame in frames:
        filtered_df = parquet_df[parquet_df.frame == frame].copy()
        filtered_df = filtered_df.sort_values(["plot_order"]).set_index("plot_order")
        traces = [go.Scatter(
            x=filtered_df['x'],
            y=filtered_df['y'],
            mode='markers',
            marker=dict(
                color=filtered_df.color,
                size=9))]

        for i, seg in enumerate(connections):
            trace = go.Scatter(
                    x=filtered_df.loc[seg]['x'],
                    y=filtered_df.loc[seg]['y'],
                    mode='lines',
            )
            traces.append(trace)
        frame_data = go.Frame(data=traces, traces = [i for i in range(17)])
        frames_l.append(frame_data)

    traces = [go.Scatter(
        x=first_frame_df['x'],
        y=first_frame_df['y'],
        mode='markers',
        marker=dict(
            color=first_frame_df.color,
            size=9
        )
    )]
    for i, seg in enumerate(connections):
        trace = go.Scatter(
            x=first_frame_df.loc[seg]['x'],
            y=first_frame_df.loc[seg]['y'],
            mode='lines',
            line=dict(
                color='black',
                width=2
            )
        )
        traces.append(trace)
    fig = go.Figure(
        data=traces,
        frames=frames_l
    )


    fig.update_layout(
        width=500,
        height=800,
        scene={
            'aspectmode': 'data',
        },
        updatemenus=[
            {
                "buttons": [
                    {
                        "args": [None, {"frame": {"duration": 100,
                                                  "redraw": True},
                                        "fromcurrent": True,
                                        "transition": {"duration": 0}}],
                        "label": "&#9654;",
                        "method": "animate",
                    },
                    {
                        "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                          "mode": "immediate",
                                          "transition": {"duration": 0}}],
                        "label": "&#9612;&#9612;",
                        "method": "animate",
                    },
                ],
                "direction": "left",
                "pad": {"r": 100, "t": 100},
                "font": {"size":20},
                "type": "buttons",
                "x": 0.1,
                "y": 0,
            }
        ],
    )
    camera = dict(
        up=dict(x=0, y=-1, z=0),
        eye=dict(x=0, y=0, z=2.5)
    )
    fig.update_layout(title_text=title, title_x=0.5)
    fig.update_layout(scene_camera=camera, showlegend=False)
    fig.update_layout(xaxis = dict(visible=False),
            yaxis = dict(visible=False),
    )
    fig.update_yaxes(autorange="reversed")

    fig.show()
    
def get_phrase(df, file_id, sequence_id):
    return df[
        np.logical_and(
            df.file_id == file_id, 
            df.sequence_id == sequence_id
        )
    ].phrase.iloc[0]

# Explore Metadata

### explore supplemental_metadata

In [38]:
# Load the supplemental_metadata.csv file into memory
supplemental_df = pd.read_csv("/kaggle/input/asl-fingerspelling/supplemental_metadata.csv")
pd.set_option('display.max_columns', None)
supplemental_df.head(3)

path   file_id  sequence_id  \
0  supplemental_landmarks/33432165.parquet  33432165   1535467051   
1  supplemental_landmarks/33432165.parquet  33432165   1535499058   
2  supplemental_landmarks/33432165.parquet  33432165   1535530550   

   participant_id                             phrase  
0             251  coming up with killer sound bites  
1             239         we better investigate this  
2             245   interesting observation was made

In [39]:
## get count phrases
phrase_count = supplemental_df["phrase"]

In [40]:
## get count of unique phrases
unique_phrase = supplemental_df["phrase"].unique()

In [41]:
print("number of phrase is : {} and number of unique phrase is : {}".format(len(phrase_count), len(unique_phrase)))

number of phrase is : 52958 and number of unique phrase is : 508


In [ ]:
# type(phrase_count),type(unique_phrase)

### create separete dataframe to store phrases and their value counts

In [42]:
# Get the value counts for the 'phrase' columns
phrase_counts = supplemental_df['phrase'].value_counts()

# Create a new DatFrame with 'phrase' and 'count' columns 
phrase_data = pd.DataFrame({'phrases': phrase_counts.index, 'phrase_count': phrase_counts.values})

In [45]:
phrase_data.head(10)

phrases  phrase_count
0          why do you ask silly questions           117
1              find a nearby parking spot           117
2            apartments are too expensive           116
3        what to do when the oil runs dry           115
4    that agreement is rife with problems           115
5             most judges are very honest           115
6             do not lie in court or else           115
7              the minimum amount of time           115
8  the biggest hamburger i have ever seen           115
9     where did you get such a silly idea           115

### visualize data for 5 most frequent and least frequent phrases

In [46]:
fig = px.bar(phrase_data.iloc[:5,:], x='phrase_count', y='phrases', color='phrases', orientation='h')
fig.update_layout(
    title={
        'text': "count of top 5 most frequent phrases",
        'y':0.96,
        'x':0.4,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    legend_title_text='Aspect:'
)

fig.show()

In [47]:
fig = px.bar(phrase_data.iloc[504:508,:], x='phrase_count', y='phrases', color='phrases', orientation='h')
fig.update_layout(
    title={
        'text': "count of 5 least phrases",
        'y':0.96,
        'x':0.4,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    legend_title_text='Aspect:'
)

fig.show()

# Explore Landmark

## loading parquest file of 

In [48]:
##create subset of dataset where phrase is "coming up with killer sound bites"
top_phrase = supplemental_df[supplemental_df["phrase"]=="coming up with killer sound bites"]['path'].values[0]
top_phrase

'supplemental_landmarks/33432165.parquet'

In [49]:
base_dir=Path("/kaggle/input/asl-fingerspelling")

### explore landmark file of top_phrase

In [50]:
landmark_file = pd.read_parquet(base_dir/top_phrase)
landmark_file.head()

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1535467051       0  0.473406  0.471368  0.476484  0.467808  0.471630   
1535467051       1  0.471909  0.471652  0.476131  0.468071  0.472056   
1535467051       2  0.474033  0.471113  0.476054  0.467614  0.471442   
1535467051       3  0.475442  0.472270  0.476926  0.468922  0.472692   
1535467051       4  0.476560  0.471422  0.475697  0.467995  0.471922   

             x_face_5  x_face_6  x_face_7  x_face_8  x_face_9  x_face_10  \
sequence_id                                                                
1535467051   0.474802  0.484624  0.407028  0.488582  0.489342   0.495933   
1535467051   0.475196  0.484882  0.406707  0.489017  0.489980   0.497027   
1535467051   0.474595  0.484442  0.406840  0.488658  0.489584   0.496417   
1535467051   0.475905  0.485815  0.407603  0.490161  0.491196   0.498345   
1535467051   0.475109  0.484853  0.406288  0.489202  0.490323   0.497825   

             x_face_11  x_face_12  x_face_13  x_face_14  x_face_15  x_face_16  \
sequence_id                                                                     
1535467051    0.473726   0.474917   0.476713   0.476836   0.476215   0.476068   
1535467051    0.472116   0.473192   0.474896   0.475086   0.474446   0.474275   
1535467051    0.474069   0.474843   0.476212   0.476304   0.475605   0.475279   
1535467051    0.475517   0.476275   0.477564   0.477704   0.477103   0.476854   
1535467051    0.476432   0.476858   0.477804   0.477938   0.477188   0.476631   

             x_face_17  x_face_18  x_face_19  x_face_20  x_face_21  x_face_22  \
sequence_id                                                                     
1535467051    0.476863   0.478874   0.473082   0.465010   0.377832   0.439035   
1535467051    0.475082   0.477186   0.473155   0.464938   0.376890   0.439271   
1535467051    0.475741   0.477268   0.472758   0.464778   0.377405   0.438962   
1535467051    0.477320   0.477510   0.473825   0.465722   0.378404   0.439784   
1535467051    0.476657   0.476171   0.472845   0.464592   0.376827   0.438730   

             x_face_23  x_face_24  x_face_25  x_face_26  x_face_27  x_face_28  \
sequence_id                                                                     
1535467051    0.426370   0.414969   0.402306   0.450253   0.424557   0.438888   
1535467051    0.426584   0.415021   0.401732   0.450421   0.424083   0.438401   
1535467051    0.426162   0.414619   0.401898   0.450310   0.424200   0.438641   
1535467051    0.426832   0.415215   0.402676   0.451306   0.425230   0.439818   
1535467051    0.425977   0.414409   0.401263   0.449931   0.424052   0.438424   

             x_face_29  x_face_30  x_face_31  x_face_32  x_face_33  x_face_34  \
sequence_id                                                                     
1535467051    0.411327   0.402938   0.391817   0.432507   0.403838   0.365630   
1535467051    0.410864   0.402452   0.391116   0.430431   0.403247   0.363964   
1535467051    0.410929   0.402523   0.391007   0.430362   0.403618   0.364887   
1535467051    0.411863   0.403396   0.391568   0.430659   0.404467   0.365399   
1535467051    0.410763   0.402247   0.390478   0.428895   0.402915   0.362936   

             x_face_35  x_face_36  x_face_37  x_face_38  x_face_39  x_face_40  \
sequence_id                                                                     
1535467051    0.381915   0.420821   0.456829   0.461179   0.442000   0.433976   
1535467051    0.380697   0.420126   0.455308   0.459461   0.440307   0.432249   
1535467051    0.381299   0.420235   0.457275   0.460752   0.441575   0.432758   
1535467051    0.382161   0.421117   0.458457   0.461939   0.442454   0.433405   
1535467051    0.380136   0.419566   0.459817   0.462572   0.443569   0.434247   

             x_face_41  x_face_42  x_face_43  x_face_44  x_face_45  x_face_46  \
sequence_id                                           

In [51]:
landmark_file=landmark_file.reset_index(inplace=False)

In [52]:
landmark_file.head()

sequence_id  frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
0   1535467051      0  0.473406  0.471368  0.476484  0.467808  0.471630   
1   1535467051      1  0.471909  0.471652  0.476131  0.468071  0.472056   
2   1535467051      2  0.474033  0.471113  0.476054  0.467614  0.471442   
3   1535467051      3  0.475442  0.472270  0.476926  0.468922  0.472692   
4   1535467051      4  0.476560  0.471422  0.475697  0.467995  0.471922   

   x_face_5  x_face_6  x_face_7  x_face_8  x_face_9  x_face_10  x_face_11  \
0  0.474802  0.484624  0.407028  0.488582  0.489342   0.495933   0.473726   
1  0.475196  0.484882  0.406707  0.489017  0.489980   0.497027   0.472116   
2  0.474595  0.484442  0.406840  0.488658  0.489584   0.496417   0.474069   
3  0.475905  0.485815  0.407603  0.490161  0.491196   0.498345   0.475517   
4  0.475109  0.484853  0.406288  0.489202  0.490323   0.497825   0.476432   

   x_face_12  x_face_13  x_face_14  x_face_15  x_face_16  x_face_17  \
0   0.474917   0.476713   0.476836   0.476215   0.476068   0.476863   
1   0.473192   0.474896   0.475086   0.474446   0.474275   0.475082   
2   0.474843   0.476212   0.476304   0.475605   0.475279   0.475741   
3   0.476275   0.477564   0.477704   0.477103   0.476854   0.477320   
4   0.476858   0.477804   0.477938   0.477188   0.476631   0.476657   

   x_face_18  x_face_19  x_face_20  x_face_21  x_face_22  x_face_23  \
0   0.478874   0.473082   0.465010   0.377832   0.439035   0.426370   
1   0.477186   0.473155   0.464938   0.376890   0.439271   0.426584   
2   0.477268   0.472758   0.464778   0.377405   0.438962   0.426162   
3   0.477510   0.473825   0.465722   0.378404   0.439784   0.426832   
4   0.476171   0.472845   0.464592   0.376827   0.438730   0.425977   

   x_face_24  x_face_25  x_face_26  x_face_27  x_face_28  x_face_29  \
0   0.414969   0.402306   0.450253   0.424557   0.438888   0.411327   
1   0.415021   0.401732   0.450421   0.424083   0.438401   0.410864   
2   0.414619   0.401898   0.450310   0.424200   0.438641   0.410929   
3   0.415215   0.402676   0.451306   0.425230   0.439818   0.411863   
4   0.414409   0.401263   0.449931   0.424052   0.438424   0.410763   

   x_face_30  x_face_31  x_face_32  x_face_33  x_face_34  x_face_35  \
0   0.402938   0.391817   0.432507   0.403838   0.365630   0.381915   
1   0.402452   0.391116   0.430431   0.403247   0.363964   0.380697   
2   0.402523   0.391007   0.430362   0.403618   0.364887   0.381299   
3   0.403396   0.391568   0.430659   0.404467   0.365399   0.382161   
4   0.402247   0.390478   0.428895   0.402915   0.362936   0.380136   

   x_face_36  x_face_37  x_face_38  x_face_39  x_face_40  x_face_41  \
0   0.420821   0.456829   0.461179   0.442000   0.433976   0.450536   
1   0.420126   0.455308   0.459461   0.440307   0.432249   0.448891   
2   0.420235   0.457275   0.460752   0.441575   0.432758   0.449593   
3   0.421117   0.458457   0.461939   0.442454   0.433405   0.450517   
4   0.419566   0.459817   0.462572   0.443569   0.434247   0.451100   

   x_face_42  x_face_43  x_face_44  x_face_45  x_face_46  x_face_47  \
0   0.443201   0.425401   0.461335   0.459824   0.388446   0.449155   
1   0.441624   0.423625   0.461606   0.460182   0.387467   0.448844   
2   0.441757   0.423778   0.461096   0.459601   0.387695   0.448770   
3   0.442474   0.424058   0.462235   0.460806   0.388729   0.449925   
4   0.442978   0.422396   0.461367   0.460024   0.387541   0.448589   

   x_face_48  x_face_49  x_face_50  x_face_51  x_face_52  x_face_53  \
0   0.438655   0.438942   0.385103   0.463460   0.414477   0.398735   
1   0.438500   0.438745   0.384049   0.463806   0.413816   0.397911   
2   0.438125   0.438299   0.384422   0.463261   0.413726   0.397919   
3   0.439181   0.439398   0.385261   0.464542   0.414799   0.398929   
4   0.438154   0.438376   0.383263   0.463706   0.414179   0.398191   

   x_face_54  x_face_55  x_face_56  x_face_57  x_face_58  x_face_59  \
0   0.386821   0.465187   0.4

In [ ]:
# len(landmark_file.columns)  ## 1630

In [53]:
landmark_file.shape

(172701, 1631)

In [ ]:
# view number of unique sequence_ids in dataset 
# landmark_file["sequence_id"].nunique() # 1000

In [54]:
# return 1st two sequence_ids
landmark_file["sequence_id"].unique()[:2]

array([1535467051, 1535499058])

In [ ]:
# landmark_file["frame"].nunique() # 507

In [55]:
#fetch landmark data for sequence id=1535467051
landmark_1st_id=landmark_file[landmark_file["sequence_id"]==1535467051]

In [56]:
landmark_1st_id

sequence_id  frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
0     1535467051      0  0.473406  0.471368  0.476484  0.467808  0.471630   
1     1535467051      1  0.471909  0.471652  0.476131  0.468071  0.472056   
2     1535467051      2  0.474033  0.471113  0.476054  0.467614  0.471442   
3     1535467051      3  0.475442  0.472270  0.476926  0.468922  0.472692   
4     1535467051      4  0.476560  0.471422  0.475697  0.467995  0.471922   
..           ...    ...       ...       ...       ...       ...       ...   
142   1535467051    142  0.481872  0.480452  0.484781  0.476917  0.480940   
143   1535467051    143  0.483839  0.479552  0.484142  0.476042  0.479986   
144   1535467051    144  0.485219  0.481192  0.485641  0.477435  0.481628   
145   1535467051    145  0.484826  0.481760  0.486053  0.477720  0.482159   
146   1535467051    146  0.484951  0.479347  0.483790  0.475579  0.479756   

     x_face_5  x_face_6  x_face_7  x_face_8  x_face_9  x_face_10  x_face_11  \
0    0.474802  0.484624  0.407028  0.488582  0.489342   0.495933   0.473726   
1    0.475196  0.484882  0.406707  0.489017  0.489980   0.497027   0.472116   
2    0.474595  0.484442  0.406840  0.488658  0.489584   0.496417   0.474069   
3    0.475905  0.485815  0.407603  0.490161  0.491196   0.498345   0.475517   
4    0.475109  0.484853  0.406288  0.489202  0.490323   0.497825   0.476432   
..        ...       ...       ...       ...       ...        ...        ...   
142  0.484109  0.493737  0.415482  0.498035  0.499096   0.506294   0.481800   
143  0.483198  0.492968  0.414613  0.497181  0.498163   0.505220   0.483738   
144  0.484757  0.494281  0.414899  0.498482  0.499509   0.506692   0.485140   
145  0.485115  0.494135  0.414605  0.498052  0.498987   0.505822   0.484739   
146  0.482840  0.492235  0.413264  0.496277  0.497203   0.504059   0.484748   

     x_face_12  x_face_13  x_face_14  x_face_15  x_face_16  x_face_17  \
0     0.474917   0.476713   0.476836   0.476215   0.476068   0.476863   
1     0.473192   0.474896   0.475086   0.474446   0.474275   0.475082   
2     0.474843   0.476212   0.476304   0.475605   0.475279   0.475741   
3     0.476275   0.477564   0.477704   0.477103   0.476854   0.477320   
4     0.476858   0.477804   0.477938   0.477188   0.476631   0.476657   
..         ...        ...        ...        ...        ...        ...   
142   0.482523   0.483913   0.483800   0.482861   0.482228   0.482521   
143   0.484292   0.485434   0.485343   0.484565   0.484061   0.484280   
144   0.485681   0.486792   0.486715   0.485997   0.485545   0.485808   
145   0.485342   0.486513   0.486422   0.485642   0.485114   0.485317   
146   0.485059   0.485874   0.485759   0.484987   0.484399   0.484311   

     x_face_18  x_face_19  x_face_20  x_face_21  x_face_22  x_face_23  \
0     0.478874   0.473082   0.465010   0.377832   0.439035   0.426370   
1     0.477186   0.473155   0.464938   0.376890   0.439271   0.426584   
2     0.477268   0.472758   0.464778   0.377405   0.438962   0.426162   
3     0.477510   0.473825   0.465722   0.378404   0.439784   0.426832   
4     0.476171   0.472845   0.464592   0.376827   0.438730   0.425977   
..         ...        ...        ...        ...        ...        ...   
142   0.485174   0.481881   0.473629   0.383475   0.447505   0.434717   
143   0.485197   0.481084   0.472899   0.383247   0.446135   0.433774   
144   0.486350   0.482675   0.474484   0.383514   0.446673   0.434150   
145   0.487338   0.483199   0.474874   0.383982   0.447202   0.434411   
146   0.484974   0.480823   0.472573   0.382917   0.445888   0.433199   

     x_face_24  x_face_25  x_face_26  x_face_27  x_face_28  x_face_29  \
0     0.414969   0.402306   0.450253   0.424557   0.438888   0.411327   
1     0.415021   0.401732   0.450421   0.424083   0.438401   0.410864   
2     0.414619   0.401898   0.450310   0.424200   0.438641   0.410929   
3     0.415215   0.402676   0.451306   0.425230   0.439818   0.411863   
4     0.4144

# explore train file

In [57]:
train_data=pd.read_csv("/kaggle/input/asl-fingerspelling/train.csv")
train_data.shape

(67208, 5)

In [58]:
train_data.head()

path  file_id  sequence_id  participant_id  \
0  train_landmarks/5414471.parquet  5414471   1816796431             217   
1  train_landmarks/5414471.parquet  5414471   1816825349             107   
2  train_landmarks/5414471.parquet  5414471   1816909464               1   
3  train_landmarks/5414471.parquet  5414471   1816967051              63   
4  train_landmarks/5414471.parquet  5414471   1817123330              89   

                      phrase  
0               3 creekhouse  
1            scales/kuhaylah  
2        1383 william lanier  
3          988 franklin lane  
4  6920 northeast 661st road

#### explore file ->/kaggle/input/asl-fingerspelling/character_to_prediction_index.json

In [59]:
char_to_pred="/kaggle/input/asl-fingerspelling/character_to_prediction_index.json"
# Python program to read
# json file
char=[]
values=[]
import json

# Opening JSON file
f = open(char_to_pred)

# returns JSON object as
# a dictionary
data = json.load(f)

# Iterating through the json
# list
for i,j in data.items():
    char.append(i)
    values.append(j)
#   print("key:"+str(i),"values:"+str(j))

# Closing file
f.close()

# print("\n characters list:",char)
# print("\n values list:",values)

In [60]:
char_to_pred_index=pd.DataFrame({"char":char,"values":values})
char_to_pred_index.head(20)

char  values
0             0
1     !       1
2     #       2
3     $       3
4     %       4
5     &       5
6     '       6
7     (       7
8     )       8
9     *       9
10    +      10
11    ,      11
12    -      12
13    .      13
14    /      14
15    0      15
16    1      16
17    2      17
18    3      18
19    4      19

# Visualizing the Sequence

### Let's get random file ID and sequence to Visualize the sequence

In [61]:
# Get number of unique file_ids in train folder
unique_file_ids = len(np.unique(supplemental_df['file_id']))

# Generate a random integer between 0 and 53 (unique_file_ids)
random_id = np.random.randint(0, unique_file_ids)

# Getting the random file_id 
random_file_id = np.unique(supplemental_df['file_id'])[random_id]

In [62]:
# Get all different sequences in random file
signs = supplemental_df[supplemental_df['file_id'] == random_file_id]

In [63]:
signs.head()

path     file_id  sequence_id  \
50958  supplemental_landmarks/2057261717.parquet  2057261717   2022159673   
50959  supplemental_landmarks/2057261717.parquet  2057261717   2022215356   
50960  supplemental_landmarks/2057261717.parquet  2057261717   2022217825   
50961  supplemental_landmarks/2057261717.parquet  2057261717   2022228161   
50962  supplemental_landmarks/2057261717.parquet  2057261717   2022325061   

       participant_id                             phrase  
50958             137  this mission statement is baloney  
50959              22      i listen to the tape everyday  
50960             250      meet tomorrow in the lavatory  
50961             184        relations are very strained  
50962             240    the registration period is over

The number of unique sequences in each .parquet file is 1000.

In [64]:
len(np.unique(signs.index))

1000

In [65]:
# Get a random Sequence id
random_squence_id = signs.sample()['sequence_id'].item()

#### Let's Load random file id to visualize the sequence 

In [66]:
path_to_sign = f"/kaggle/input/asl-fingerspelling/supplemental_landmarks/{random_file_id}.parquet"
parquet = pd.read_parquet(path_to_sign)

In [67]:
sequence = parquet[parquet.index == random_squence_id]
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
2026593338       0  0.730082  0.703397  0.712658  0.687117  0.701499   
2026593338       1  0.747519  0.729905  0.738497  0.715452  0.728341   
2026593338       2  0.751308  0.728350  0.738703  0.713160  0.726333   
2026593338       3  0.745351  0.723377  0.734193  0.709440  0.721543   
2026593338       4  0.760071  0.736351  0.747295  0.722334  0.734460   
...            ...       ...       ...       ...       ...       ...   
2026593338     204  0.820164  0.790680  0.800929  0.778059  0.789675   
2026593338     205  0.818855  0.790992  0.800983  0.778673  0.790104   
2026593338     206  0.822533  0.799431  0.809006  0.785894  0.798423   
2026593338     207  0.818316  0.788487  0.799290  0.776982  0.787586   
2026593338     208  0.818086  0.785438  0.796793  0.774097  0.784425   

             x_face_5  x_face_6  x_face_7  x_face_8  x_face_9  x_face_10  \
sequence_id                                                                
2026593338   0.703313  0.711472  0.578414  0.713020  0.711743   0.710387   
2026593338   0.730058  0.738072  0.600214  0.739890  0.738906   0.739528   
2026593338   0.728344  0.737199  0.602083  0.738664  0.737079   0.735362   
2026593338   0.724072  0.734153  0.593961  0.736185  0.734737   0.734404   
2026593338   0.736896  0.746985  0.608533  0.748672  0.747247   0.746365   
...               ...       ...       ...       ...       ...        ...   
2026593338   0.793205  0.805949  0.662421  0.809663  0.809364   0.812234   
2026593338   0.793694  0.806756  0.656677  0.810827  0.810839   0.814388   
2026593338   0.801484  0.812839  0.661826  0.816036  0.815723   0.818057   
2026593338   0.791511  0.805640  0.659299  0.810246  0.810325   0.814515   
2026593338   0.788530  0.803219  0.657837  0.807693  0.807595   0.811373   

             x_face_11  x_face_12  x_face_13  x_face_14  x_face_15  x_face_16  \
sequence_id                                                                     
2026593338    0.730498   0.730738   0.730885   0.730793   0.731490   0.731977   
2026593338    0.748131   0.749012   0.749964   0.750081   0.750524   0.751015   
2026593338    0.751858   0.752658   0.753640   0.753573   0.754076   0.754705   
2026593338    0.745966   0.746956   0.748123   0.748099   0.748507   0.749096   
2026593338    0.760540   0.761347   0.762304   0.762369   0.762721   0.763236   
...                ...        ...        ...        ...        ...        ...   
2026593338    0.820498   0.820682   0.820918   0.821177   0.821794   0.822255   
2026593338    0.819111   0.819338   0.819704   0.819830   0.820283   0.820622   
2026593338    0.822617   0.822779   0.823153   0.823243   0.823443   0.823547   
2026593338    0.818694   0.819058   0.819501   0.819634   0.820187   0.820711   
2026593338    0.818264   0.818343   0.818544   0.818817   0.819179   0.819404   

             x_face_17  x_face_18  x_face_19  x_face_20  x_face_21  x_face_22  \
sequence_id                                                                     
2026593338    0.732443   0.724175   0.706956   0.691230   0.485356   0.633966   
2026593338    0.751924   0.748973   0.733054   0.719096   0.528344   0.658400   
2026593338    0.755670   0.753412   0.732059   0.717269   0.528293   0.658306   
2026593338    0.750217   0.747996   0.727267   0.712839   0.528048   0.654491   
2026593338    0.764234   0.762554   0.740199   0.726283   0.537019   0.667742   
...                ...        ...        ...        ...        ...        ...   
2026593338    0.822840   0.807779   0.794041   0.777189   0.592349   0.720675   
2026593338    0.821140   0.807647   0.794239   0.777767   0.590596   0.721070   
2026593338    0.823857   0.815950   0.802562   0.786049   0.593233   0.724629   
2026593338    0.821464   0.806018   0.792010   0.775625   0.594323   0.722683   
2026593338    0.819778   0.804484   0.789103   0.772757   0.5

In [68]:
sequence_phrase = get_phrase(supplemental_df, random_file_id, random_squence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")

: 

## _________________________THANK YOU !!! ___________________

please upvote if you like my work.